# COVID19 - District Region of Sao Paulo State, Brazil

In [1]:
from environs import Env
env = Env()
env.str("CUDA_DEVICE_ORDER",'PCI_BUS_ID')
env.str("CUDA_VISIBLE_DEVICES",'0,1,2,3,4')
env.int("NUMBA_ENABLE_CUDASIM",1)
env.bool("OMPI_MCA_opal_cuda_support",True)

import os
import ray
# MB=1024*1024
# GB=MB*1024
# ray.init(num_gpus=5,num_cpus=1)
# @ray.remote(num_gpus=1)
# def use_gpu():
#     print("ray.get_gpu_ids(): {}".format(ray.get_gpu_ids()[0]))
#     print("CUDA_VISIBLE_DEVICES: {}".format(os.environ["CUDA_VISIBLE_DEVICES"]))

# use_gpu.remote()


ray.shutdown()
ray.init()

2021-02-24 10:48:57,298	INFO services.py:1092 -- View the Ray dashboard at http://127.0.0.1:8266


{'node_ip_address': '192.168.0.104',
 'raylet_ip_address': '192.168.0.104',
 'redis_address': '192.168.0.104:61667',
 'object_store_address': '/tmp/ray/session_2021-02-24_10-48-56_739247_23456/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2021-02-24_10-48-56_739247_23456/sockets/raylet',
 'webui_url': '127.0.0.1:8266',
 'session_dir': '/tmp/ray/session_2021-02-24_10-48-56_739247_23456',
 'metrics_export_port': 60683,
 'node_id': 'e998188323179f9069013f344f13d14abaa1256b'}

In [2]:
import urllib.request
import pandas as pd
import numpy as np
from datetime import datetime,timedelta,date

In [3]:
# Download data
import get_data
LoadData=False

if LoadData:
    get_data.get_data()

In [4]:
dfSP = pd.read_csv("data/dados_municipios_SP.csv.gz",compression='gzip')
query=dfSP.query('DRS == "{}"'.format('DRS 01 - Grande São Paulo'))
query2=query[query['date']=="2020-12-27"]
display(query2)
display(query2['popEst'].sum())

date state                    city place_type  confirmed  \
10735   2020-12-27    SP                   Arujá       city       2812   
15873   2020-12-27    SP                 Barueri       city      11200   
19037   2020-12-27    SP          Biritiba Mirim       city        557   
26481   2020-12-27    SP                Caieiras       city       3258   
27044   2020-12-27    SP                 Cajamar       city       1850   
31604   2020-12-27    SP             Carapicuíba       city      11966   
38283   2020-12-27    SP                   Cotia       city       5679   
41274   2020-12-27    SP                 Diadema       city      11367   
45435   2020-12-27    SP          Embu das Artes       city       4485   
45751   2020-12-27    SP              Embu-Guaçu       city       1710   
49346   2020-12-27    SP   Ferraz de Vasconcelos       city       5041   
50918   2020-12-27    SP        Francisco Morato       city       3756   
51228   2020-12-27    SP         Franco da Rocha       city       3415   
55589   2020-12-27    SP               Guararema       city        604   
57343   2020-12-27    SP               Guarulhos       city      27346   
69950   2020-12-27    SP    Itapecerica da Serra       city       3330   
70872   2020-12-27    SP                 Itapevi       city       4033   
72533   2020-12-27    SP         Itaquaquecetuba       city       5421   
78722   2020-12-27    SP                 Jandira       city       2383   
81841   2020-12-27    SP               Juquitiba       city       1295   
89022   2020-12-27    SP               Mairiporã       city       2565   
91740   2020-12-27    SP                    Mauá       city      10974   
95945   2020-12-27    SP         Mogi das Cruzes       city      11297   
106914  2020-12-27    SP                  Osasco       city      18753   
120725  2020-12-27    SP   Pirapora do Bom Jesus       city        748   
125938  2020-12-27    SP                     Poá       city       2789   
133599  2020-12-27    SP          Ribeirão Pires       city       3052   
135888  2020-12-27    SP     Rio Grande da Serra       city        837   
139016  2020-12-27    SP             Salesópolis       city        291   
144279  2020-12-27    SP            Santa Isabel       city       1816   
146657  2020-12-27    SP     Santana de Parnaíba       city       4987   
147261  2020-12-27    SP             Santo André       city      27216   
153816  2020-12-27    SP                  Suzano       city       7372   
154628  2020-12-27    SP   São Bernardo do Campo       city      33418   
154949  2020-12-27    SP      São Caetano do Sul       city       7385   
158597  2020-12-27    SP   São Lourenço da Serra       city        321   
159773  2020-12-27    SP               São Paulo       city     391917   
162730  2020-12-27    SP         Taboão da Serra       city       9873   
174966  2020-12-27    SP  Vargem Grande Paulista       city        819   

        deaths  order_for_place  is_last      popEst  estimated_population  \
10735      111              262    False     89824.0               91157.0   
15873      440              266    False    274182.0              276982.0   
19037       33              236    False     32598.0               32936.0   
26481      109              263    False    101470.0              102775.0   
27044       84              260    False     76801.0               77934.0   
31604      435              268    False    400927.0              403183.0   
38283      230              266    False    249210.0              253608.0   
41274      479              261    False    423884.0              426757.0   
45435      208              263    False    273726.0              276535.0   
45751       58              253    False     69385.0               69901.0   
49346      152              270    False    194276.0              196500.0   
50918      148              257    False    175844.0              177633.0   
51228      138              259    Fals

21734682.0

# Model

In [5]:
# lista DRSs
DRS = list(dfSP["DRS"].unique())
DRS.remove("Indefinido")
DRS

['DRS 09 - Marília',
 'DRS 15 - São José do Rio Preto',
 'DRS 14 - São João da Boa Vista',
 'DRS 06 - Bauru',
 'DRS 16 - Sorocaba',
 'DRS 11 - Presidente Prudente',
 'DRS 05 - Barretos',
 'DRS 13 - Ribeirão Preto',
 'DRS 02 - Araçatuba',
 'DRS 07 - Campinas',
 'DRS 03 - Araraquara',
 'DRS 10 - Piracicaba',
 'DRS 17 - Taubaté',
 'DRS 08 - Franca',
 'DRS 01 - Grande São Paulo',
 'DRS 12 - Registro',
 'DRS 04 - Baixada Santista']

# SEAIR-D Model Equations

$$\Large \begin{array}{l}
\dfrac{d s}{d t}=-[ i(t) + \beta_R \cdot a(t)] \cdot \beta \cdot s(t)\\ 
\dfrac{d e}{d t}=[i(t) + \beta_R \cdot a(t)] \cdot \beta \cdot s(t) -\sigma \cdot e(t) - \mu \cdot e(t)\\ 
\dfrac{d a}{d t}=\sigma \cdot e(t) \cdot (1-p)-\gamma \cdot a(t)  - \mu \cdot a(t)\\
\dfrac{d i}{d t}=\sigma \cdot e(t) \cdot p - \gamma \cdot i(t)  - \mu \cdot i(t)\\ 
\dfrac{d r}{d t}=b_\gamma \cdot i(t) + \gamma \cdot a(t) + \nu \cdot k(t)\\
\dfrac{d k}{d t}=(a_\gamma + \nu ) \cdot k(t) + \mu \cdot [e(t)+a(t)+i(t)]
\end{array}$$

The recovery and death rates are calculated from $\gamma$

$$\Large \gamma=a_\gamma+b_\gamma$$

The sigmoid function:

$$\Large S(t)=\frac{1}{1 + e^{-t}}$$

The $\sigma$ variation is modeled as

$$\Large 
    \sigma = \sigma_i \cdot [1-S(t)]+\sigma_f \cdot S(t)
$$

See below the transition between two value - $\sigma_i$ and $\sigma_f$ -  based on Sigmoids Curves when $\sigma_i$<$\sigma_f$, which is indicated by the blue curve, and $\sigma_i$>$\sigma_f$, which is indicated by the red curve.

![Sigmoids Curves when $\sigma_i$<$\sigma_f$ and $\sigma_i$>$\sigma_f$](../countries/results/sigmoid.png)
<h4><center>Sigmoids Curves when $\sigma_i$<$\sigma_f$ and $\sigma_i$>$\sigma_f$</center></h4>


The $\sigma$ with sigmoid is performed two times inside the data interval, so we have an initial value constant of $\sigma_i$, a sigmoid transition to value $\sigma_f$, a period of $\sigma_f$ constant, after a sigmoid transition to value $\sigma_{ff}$ and a period of $\sigma_{ff}$ constant. The times where the two sigmoids are placed are calculated by optimization as well as the values of $\sigma_i$,$\sigma_f$ and $\sigma_{ff}$.

The sum of all people accounted is equal to population considered:

$$\Large s + e + a + i + r + k = N$$

The derivate is:

$$\Large \frac{d s}{d t}+\frac{d e}{d t}+\frac{d a}{d t}+\frac{d i}{d t}+\frac{d r}{d t}+\frac{d k}{d t} = 0$$

The last equation does not need to be solve because:

$$\Large \frac{d k}{d t}=-(\frac{d s}{d t}+\frac{d e}{d t}+\frac{d a}{d t}+\frac{d i}{d t}+\frac{d r}{d t})$$

The sum of all rates are equal to zero! The importance of this equation is that it conservates the rates.


## Parameters

### Fixed parameters:

N: the population considered in the study

$p$: is the fraction of the exposed which become symptomatic infectious sub-population.

$(1-p)$: is the fraction of the exposed which becomes asymptomatic infectious sub-population.

### Optimized Parameters

All parameters below are calculated through evolutionary optimization package Yabox to fit real data:

$\beta$: Effective contact rate [1/day]

$\beta_R$: Fraction of effective contact rate [1/day]
    
$\gamma$: Recovery(+Mortality) rate $\gamma=(a_\gamma+b_\gamma)$ [1/day]

$a_\gamma$: mortality of infected  [1/day]

$b_\gamma$: recovery rate  [1/day]

$\sigma$: is the rate at which individuals move from the exposed to the infectious classes. Three parameters $\sigma_i$, $\sigma_f$ and $\sigma_{ff}$ are used along the days. The transition from $\sigma_i$ to $\sigma_f$ and from $\sigma_f$ to $\sigma_{ff}$ are made by a sigmoid function. Its reciprocal  ($1/\sigma$) is the average latent (exposed) period. [1/day]

$\nu$: medicine and hospital improvement rate [1/day] 

$\mu$: direct mortality rate [1/day] 

## Options: Param.CSV file, changeCSV, Adjust Param, Save CSV, Select Specific DRS

In [6]:
from IPython.display import display, HTML, Markdown

paramOpt=2
changeCSV=True
adjustParam=False
paramSave=False
selectDRS=False

## Different Options to Load Param.CSV file

In [7]:
if paramOpt==-1:
    paramFile="data/param.csv"
    version = "-1"
    model = "ManualIC"
    
if paramOpt==0:
    paramFile= "data/param_optimized_Yabox_HistMin.csv"
    version = "0"
    model = "LastIC"
    
if paramOpt==1:
    version = "116"
    model = "YaboxIC"    
    paramFile="data/param_optimized_Yabox_HistMin"+version+".csv"

if paramOpt==2:
    version = "119"
    model = "YaboxIC"    
    paramFile="data/param_optimized_Yabox_HistMin"+version+".csv"


In [8]:
dfparam = pd.read_csv(paramFile)
dfparam = dfparam.dropna()
dfparam.e0=0
dfparam.r0=0

display(Markdown("## Original Initial Parameters"))
display(dfparam)

## Original Initial Parameters

DRS  start-date  prediction-range        s0  \
0        DRS 01 - Grande São Paulo  2020-03-19               200  16376120   
1               DRS 02 - Araçatuba  2020-03-31               200    332464   
2              DRS 03 - Araraquara  2020-03-31               200    661992   
3        DRS 04 - Baixada Santista  2020-03-30               200    616626   
4                DRS 05 - Barretos  2020-03-29               200    209300   
5                   DRS 06 - Bauru  2020-04-02               200   1745532   
6                DRS 07 - Campinas  2020-04-04               200   3651744   
7                  DRS 08 - Franca  2020-03-31               200    589580   
8                 DRS 09 - Marília  2020-03-30               200    754974   
9              DRS 10 - Piracicaba  2020-03-30               200   1229207   
10    DRS 11 - Presidente Prudente  2020-03-29               200    583376   
11               DRS 12 - Registro  2020-04-03               200    225584   
12         DRS 13 - Ribeirão Preto  2020-03-28               200   1038023   
13  DRS 14 - São João da Boa Vista  2020-03-30               200    602971   
14  DRS 15 - São José do Rio Preto  2020-03-29               200    662789   
15               DRS 16 - Sorocaba  2020-03-29               200   2158190   
16                DRS 17 - Taubaté  2020-03-29               200   1867518   

    e0  a0   i0  r0   d0  START  RATIO  WCASES  WREC  
0    0   0  154   0   39    100   0.15  0.2352   0.0  
1    0   0   53   0  152    166   0.15  0.3021   0.0  
2    0   0  137   0   48     37   0.15  0.2498   0.0  
3    0   0  225   0  240     18   0.15  0.5697   0.0  
4    0   0  100   0   60    144   0.15  0.6309   0.0  
5    0   0   73   0  157      1   0.15  0.6113   0.0  
6    0   0  197   0   61      4   0.15  0.1978   0.0  
7    0   0  126   0  143    189   0.15  0.2520   0.0  
8    0   0   76   0  125     33   0.15  0.2127   0.0  
9    0   0  195   0   70     17   0.15  0.3223   0.0  
10   0   0  113   0   23    172   0.15  0.2069   0.0  
11   0   0  137   0   82     32   0.15  0.2627   0.0  
12   0   0  142   0   94    149   0.15  0.4660   0.0  
13   0   0  105   0   93    219   0.15  0.2462   0.0  
14   0   0   78   0  224     67   0.15  0.5108   0.0  
15   0   0  188   0  199    141   0.15  0.3081   0.0  
16   0   0  128   0  225    145   0.15  0.2565   0.0

## Modify param.csv file to fit better the data

In [9]:
#     dfparam['s0'] = pd.to_numeric(dfparam['s0'],errors='coerce')
#     dfparam['i0'] = pd.to_numeric(dfparam['i0'],errors='coerce')
#     dfparam['d0'] = pd.to_numeric(dfparam['d0'],errors='coerce')
#     dfparam['s0'] = dfparam['s0'].astype(float)
#     dfparam['i0'] = dfparam['i0'].astype(float)
#     dfparam['d0'] = dfparam['d0'].astype(float)
#     dfparam.loc[dfparam.DRS=='DRS 14 - São João da Boa Vista','s0'] = dfparam.loc[dfparam.DRS=='DRS 14 - São João da Boa Vista','s0'].values[0]*1.1
#     dfparam.loc[dfparam.DRS=='DRS 14 - São João da Boa Vista','i0'] = dfparam.loc[dfparam.DRS=='DRS 14 - São João da Boa Vista','i0']*.1

if changeCSV and (paramOpt==1):
    dfparam.loc[dfparam.DRS=='DRS 12 - Registro','s0'] = dfparam.loc[dfparam.DRS=='DRS 12 - Registro','s0']*2
    dfparam.loc[dfparam.DRS=='DRS 12 - Registro','d0'] = dfparam.loc[dfparam.DRS=='DRS 12 - Registro','d0']/10
    
if adjustParam:
    sCorrect=[1.38,1.0,1.05,1.5,1.5,1.4,1.1,1.5,1.15,1.55,1.35,1.2,1.35,1.15,1.55,1.45,1.25]
    dfparam.s0=dfparam.s0.multiply(sCorrect[:len(DRS)], axis=0)

if selectDRS and paramOpt==1:
    DRS=['DRS 09 - Marília','DRS 10 - Piracicaba','DRS 14 - São João da Boa Vista']

if not selectDRS:
    DRS=dfparam.DRS    

dfparam['s0'] = dfparam['s0'].astype(int)
dfparam['i0'] = dfparam['i0'].astype(int)
dfparam['d0'] = dfparam['d0'].astype(int)
dfparam['r0'] = dfparam['r0'].astype(int)

if paramSave:
    dfparam.to_csv("new_"+paramFile)    
    
display(Markdown("## Modified Initial Parameters"))

# dfparam['WREC']=dfparam['WREC'].apply(lambda x: min(x,0.001))
dfparam['WDTH']=1-dfparam['WCASES']-dfparam['WREC']

finalDate = date.today() + timedelta(days=-1)
finalDateStr = datetime.strftime(finalDate, "%Y-%m-%d")
dfparam['endDate']=finalDateStr

#poe RATIO no final
l=[0,1,2,3,4,5,6,7,8,9,11,12, 13, 14, 10] # index order
dfparam=dfparam[[dfparam.columns[i] for i in l]]

# for i in DRS:
#     query=dfSP.query('DRS == "{}"'.format(i))
#     query2=query[query['date']=="2020-12-28"]
#     dfparam.loc[dfparam['DRS']==i,'s0']=int(query2['popEst'].sum()*0.7)
    
display(dfparam)


## Modified Initial Parameters

DRS  start-date  prediction-range        s0  \
0        DRS 01 - Grande São Paulo  2020-03-19               200  16376120   
1               DRS 02 - Araçatuba  2020-03-31               200    332464   
2              DRS 03 - Araraquara  2020-03-31               200    661992   
3        DRS 04 - Baixada Santista  2020-03-30               200    616626   
4                DRS 05 - Barretos  2020-03-29               200    209300   
5                   DRS 06 - Bauru  2020-04-02               200   1745532   
6                DRS 07 - Campinas  2020-04-04               200   3651744   
7                  DRS 08 - Franca  2020-03-31               200    589580   
8                 DRS 09 - Marília  2020-03-30               200    754974   
9              DRS 10 - Piracicaba  2020-03-30               200   1229207   
10    DRS 11 - Presidente Prudente  2020-03-29               200    583376   
11               DRS 12 - Registro  2020-04-03               200    225584   
12         DRS 13 - Ribeirão Preto  2020-03-28               200   1038023   
13  DRS 14 - São João da Boa Vista  2020-03-30               200    602971   
14  DRS 15 - São José do Rio Preto  2020-03-29               200    662789   
15               DRS 16 - Sorocaba  2020-03-29               200   2158190   
16                DRS 17 - Taubaté  2020-03-29               200   1867518   

    e0  a0   i0  r0   d0  START  WCASES  WREC    WDTH     endDate  RATIO  
0    0   0  154   0   39    100  0.2352   0.0  0.7648  2021-02-23   0.15  
1    0   0   53   0  152    166  0.3021   0.0  0.6979  2021-02-23   0.15  
2    0   0  137   0   48     37  0.2498   0.0  0.7502  2021-02-23   0.15  
3    0   0  225   0  240     18  0.5697   0.0  0.4303  2021-02-23   0.15  
4    0   0  100   0   60    144  0.6309   0.0  0.3691  2021-02-23   0.15  
5    0   0   73   0  157      1  0.6113   0.0  0.3887  2021-02-23   0.15  
6    0   0  197   0   61      4  0.1978   0.0  0.8022  2021-02-23   0.15  
7    0   0  126   0  143    189  0.2520   0.0  0.7480  2021-02-23   0.15  
8    0   0   76   0  125     33  0.2127   0.0  0.7873  2021-02-23   0.15  
9    0   0  195   0   70     17  0.3223   0.0  0.6777  2021-02-23   0.15  
10   0   0  113   0   23    172  0.2069   0.0  0.7931  2021-02-23   0.15  
11   0   0  137   0   82     32  0.2627   0.0  0.7373  2021-02-23   0.15  
12   0   0  142   0   94    149  0.4660   0.0  0.5340  2021-02-23   0.15  
13   0   0  105   0   93    219  0.2462   0.0  0.7538  2021-02-23   0.15  
14   0   0   78   0  224     67  0.5108   0.0  0.4892  2021-02-23   0.15  
15   0   0  188   0  199    141  0.3081   0.0  0.6919  2021-02-23   0.15  
16   0   0  128   0  225    145  0.2565   0.0  0.7435  2021-02-23   0.15

## Solver Loading

In [10]:
%reload_ext autoreload
%autoreload 2
import LearnerYabox_v5NewModel as Learner #Yabox

2021-02-24 10:49:04,301	INFO services.py:1092 -- View the Ray dashboard at http://127.0.0.1:8266


## All Districts and Select District to Run

In [11]:
allDistricts=True
cleanRecovered=False

if allDistricts:
    display(DRS)
else:
    districtRegionSelected="DRS 01 - Grande São Paulo"
    display(districtRegionSelected)

0          DRS 01 - Grande São Paulo
1                 DRS 02 - Araçatuba
2                DRS 03 - Araraquara
3          DRS 04 - Baixada Santista
4                  DRS 05 - Barretos
5                     DRS 06 - Bauru
6                  DRS 07 - Campinas
7                    DRS 08 - Franca
8                   DRS 09 - Marília
9                DRS 10 - Piracicaba
10      DRS 11 - Presidente Prudente
11                 DRS 12 - Registro
12           DRS 13 - Ribeirão Preto
13    DRS 14 - São João da Boa Vista
14    DRS 15 - São José do Rio Preto
15                 DRS 16 - Sorocaba
16                  DRS 17 - Taubaté
Name: DRS, dtype: object

In [12]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines){
    return true;}

<IPython.core.display.Javascript object>

# Main Loop

In [13]:
if allDistricts:

    if selectDRS:
        loop=[0,len(DRS)]        
    else:
        loop=[0,6,12,17]
    
    for i in range(0,len(loop)-1):
        results=[]
        for districtRegion in DRS[loop[i]:loop[i+1]]:
            query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
            parameters = np.array(query.iloc[:, 2:])[0]
            dR=ray.put(districtRegion)
            cR=ray.put(cleanRecovered)
            vR=ray.put(version)
            f=Learner.Learner.remote(dR, *parameters, cR, vR)
            result = f.train.remote() 
            results.append(result)
        display("Running DRS {:d} to {:d}".format(loop[i]+1,loop[i+1]))
        display(DRS[loop[i]:loop[i+1]])
        resultsFinal = ray.get(results)

else:
    results=[]
    districtRegion= districtRegionSelected 
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    dR=ray.put(districtRegion)
    cR=ray.put(cleanRecovered)
    vR=ray.put(version)
    f=Learner.Learner.remote(dR, *parameters, cR, vR)
    result = f.train.remote() 
    results.append(result)
    display(districtRegion)
    resultsFinal = ray.get(results)


'Running DRS 1 to 6'

0    DRS 01 - Grande São Paulo
1           DRS 02 - Araçatuba
2          DRS 03 - Araraquara
3    DRS 04 - Baixada Santista
4            DRS 05 - Barretos
5               DRS 06 - Bauru
Name: DRS, dtype: object

  0%|          | 0/10125000.0 [00:00<?, ?it/s]
  0%|          | 0/10125000.0 [00:00<?, ?it/s]
  0%|          | 0/10125000.0 [00:00<?, ?it/s]
  0%|          | 0/10125000.0 [00:00<?, ?it/s]
  0%|          | 0/10125000.0 [00:00<?, ?it/s]
  0%|          | 0/10125000.0 [00:00<?, ?it/s]
  0%|          | 0/10125000.0 [00:01<?, ?it/s]
  0%|          | 0/10125000.0 [00:01<?, ?it/s]
  0%|          | 0/10125000.0 [00:01<?, ?it/s]
  0%|          | 0/10125000.0 [00:01<?, ?it/s]
  0%|          | 0/10125000.0 [00:01<?, ?it/s]
  0%|          | 0/10125000.0 [00:01<?, ?it/s]
  0%|          | 1/10125000.0 [00:01<1187:01:39,  2.37it/s]
  0%|          | 1/10125000.0 [00:01<1205:56:33,  2.33it/s]
  0%|          | 1/10125000.0 [00:01<1252:59:40,  2.24it/s]
  0%|          | 1/10125000.0 [00:01<1211:54:44,  2.32it/s]
  0%|          | 1/10125000.0 [00:01<1374:37:31,  2.05it/s]
  0%|          | 3/10125000.0 [00:01<1000:56:28,  2.81it/s]
  0%|          | 3/10125000.0 [00:02<1028:42:32,  2.73it/s]
  0%|          |

  0%|          | 276/10125000.0 [00:12<70:10:49, 40.07it/s]
  0%|          | 300/10125000.0 [00:12<65:07:38, 43.18it/s]
  0%|          | 231/10125000.0 [00:12<89:12:55, 31.52it/s]
  0%|          | 300/10125000.0 [00:12<67:11:18, 41.86it/s]
  0%|          | 300/10125000.0 [00:12<66:20:55, 42.39it/s]
  0%|          | 190/10125000.0 [00:12<109:26:09, 25.70it/s]
  0%|          | 300/10125000.0 [00:12<65:32:58, 42.91it/s]
  0%|          | 325/10125000.0 [00:13<61:49:05, 45.49it/s]
  0%|          | 325/10125000.0 [00:13<64:23:18, 43.68it/s]
  0%|          | 325/10125000.0 [00:13<63:43:50, 44.13it/s]
  0%|          | 253/10125000.0 [00:13<85:08:20, 33.03it/s]
  0%|          | 325/10125000.0 [00:13<61:10:43, 45.97it/s]
  0%|          | 210/10125000.0 [00:13<102:45:35, 27.37it/s]
  0%|          | 351/10125000.0 [00:13<59:04:44, 47.60it/s]
  0%|          | 351/10125000.0 [00:13<60:29:37, 46.49it/s]
  0%|          | 351/10125000.0 [00:13<60:55:55, 46.16it/s]
  0%|          | 276/10125000.0 [00:13

  0%|          | 1176/10125000.0 [00:25<33:08:32, 84.85it/s]
  0%|          | 1176/10125000.0 [00:25<32:39:02, 86.13it/s]
  0%|          | 741/10125000.0 [00:25<54:26:05, 51.66it/s]
  0%|          | 1176/10125000.0 [00:25<35:10:08, 79.96it/s]
  0%|          | 946/10125000.0 [00:25<42:22:53, 66.36it/s]
  0%|          | 1225/10125000.0 [00:25<32:38:41, 86.14it/s]
  0%|          | 1225/10125000.0 [00:25<32:49:34, 85.67it/s]
  0%|          | 1225/10125000.0 [00:25<31:41:50, 88.72it/s]
  0%|          | 780/10125000.0 [00:25<53:13:37, 52.84it/s]
  0%|          | 1225/10125000.0 [00:26<34:47:28, 80.83it/s]
  0%|          | 990/10125000.0 [00:26<41:32:56, 67.68it/s]
  0%|          | 1275/10125000.0 [00:26<31:37:34, 88.92it/s]
  0%|          | 1275/10125000.0 [00:26<32:36:29, 86.24it/s]
  0%|          | 1275/10125000.0 [00:26<31:06:43, 90.39it/s]
  0%|          | 820/10125000.0 [00:26<51:04:35, 55.06it/s]
  0%|          | 1326/10125000.0 [00:26<30:58:19, 90.80it/s]
  0%|          | 1275/1012500

...

 93%|█████████▎| 9398280/10125000.0 [42:23<01:15, 9588.19it/s]
 93%|█████████▎| 9402616/10125000.0 [42:24<01:14, 9640.24it/s]
 93%|█████████▎| 9406953/10125000.0 [42:24<01:14, 9690.84it/s]


(pid=2376) warning: basinhopping: local minimization failure
(pid=2376) basinhopping step 30: f 842564 trial_f 842564 accepted 1  lowest_f 842564
(pid=2376) districtRegion DRS 16 - Sorocaba
(pid=2376) under notifications cases 1.00
(pid=2376) under notifications deaths 1.00


 93%|█████████▎| 9411291/10125000.0 [42:25<01:14, 9634.69it/s]
 93%|█████████▎| 9415630/10125000.0 [42:25<01:14, 9529.23it/s]
 93%|█████████▎| 9419970/10125000.0 [42:26<01:13, 9545.88it/s]
 93%|█████████▎| 9424311/10125000.0 [42:26<01:12, 9643.92it/s]
 93%|█████████▎| 9428653/10125000.0 [42:26<01:12, 9606.46it/s]
 93%|█████████▎| 9432996/10125000.0 [42:27<01:10, 9749.56it/s]
 93%|█████████▎| 9437340/10125000.0 [42:27<01:11, 9634.71it/s]
 93%|█████████▎| 9441685/10125000.0 [42:28<01:11, 9559.15it/s]
 93%|█████████▎| 9446031/10125000.0 [42:28<01:12, 9370.98it/s]
 93%|█████████▎| 9450378/10125000.0 [42:29<01:11, 9407.42it/s]
 93%|█████████▎| 9454726/10125000.0 [42:29<01:10, 9487.11it/s]
 93%|█████████▎| 9459075/10125000.0 [42:30<01:10, 9438.20it/s]
 93%|█████████▎| 9463425/10125000.0 [42:30<01:09, 9586.88it/s]
 94%|█████████▎| 9467776/10125000.0 [42:31<01:07, 9768.09it/s]
 94%|█████████▎| 9472128/10125000.0 [42:31<01:06, 9871.48it/s]
 94%|█████████▎| 9476481/10125000.0 [42:31<01:05, 9889.

 99%|█████████▊| 9979278/10125000.0 [43:20<00:13, 10975.17it/s]
 99%|█████████▊| 9979278/10125000.0 [43:33<00:13, 10975.17it/s]
 99%|█████████▊| 9983746/10125000.0 [43:43<03:47, 620.94it/s]  
 99%|█████████▊| 9988215/10125000.0 [43:44<02:38, 864.54it/s]
 99%|█████████▊| 9992685/10125000.0 [43:44<01:51, 1191.77it/s]
 99%|█████████▊| 9997156/10125000.0 [43:45<01:18, 1624.55it/s]
 99%|█████████▉| 10001628/10125000.0 [43:45<00:56, 2177.30it/s]
 99%|█████████▉| 10006101/10125000.0 [43:46<00:41, 2856.85it/s]
 99%|█████████▉| 10010575/10125000.0 [43:46<00:31, 3649.94it/s]
 99%|█████████▉| 10015050/10125000.0 [43:46<00:24, 4555.27it/s]
 99%|█████████▉| 10019526/10125000.0 [43:47<00:19, 5502.83it/s]
 99%|█████████▉| 10024003/10125000.0 [43:47<00:15, 6485.14it/s]
 99%|█████████▉| 10028481/10125000.0 [43:48<00:13, 7396.95it/s]
 99%|█████████▉| 10032960/10125000.0 [43:48<00:11, 8194.59it/s]
 99%|█████████▉| 10037440/10125000.0 [43:48<00:09, 8887.67it/s]
 99%|█████████▉| 10041921/10125000.0 [43:49<

(pid=2369) basinhopping step 0: f 29063.1
(pid=2369) basinhopping step 1: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) found new global minimum on step 1 with function value 29063.1
(pid=2369) basinhopping step 2: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) basinhopping step 3: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) found new global minimum on step 3 with function value 29063.1
(pid=2369) basinhopping step 4: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) basinhopping step 5: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) basinhopping step 6: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) basinhopping step 7: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) basinhopping step 8: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) basinhopping step 9: f 29063.1 trial_f 29063.1 accepted 1  lowest_f 29063.1
(pid=2369) basinhopping ste

In [14]:
ray.shutdown()

2021-02-24 13:02:20,442	INFO services.py:1092 -- View the Ray dashboard at http://127.0.0.1:8266


# Save Results in CSV format 

In [15]:
# Save data as csv
import glob
import os

path = './results/data'
files = glob.glob(os.path.join(path, "*"+version+".csv"))
display(files)

df = (pd.read_csv(f).assign(DRS = f.split(" - ")[-1].split(version)[0]) for f in files)
df_all_drs = pd.concat(df, ignore_index=True)
df_all_drs.index.name = 'index'
df_all_drs.to_csv('./data/SEAIRD_sigmaOpt_AllDRS'+version+'.csv', sep=",")

['./results/data/SEAIRD_sigmaOpt_DRS 09 - Marilia118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 04 - Baixada Santista118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 01 - Grande Sao Paulo118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 12 - Registro118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 03 - Araraquara118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 06 - Bauru118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 05 - Barretos118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 02 - Aracatuba118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 08 - Franca118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 11 - Presidente Prudente118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 07 - Campinas118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 10 - Piracicaba118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 14 - Sao Joao da Boa Vista118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 15 - Sao Jose do Rio Preto118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 13 - Ribeirao Preto118.csv',
 './results/data/SEAIRD_sigmaOpt_DRS 16 - 